# Local HDG variational formulation

implementing LDG via HDG

In [ ]:
from ngsolve import *
from ngsolve.webgui import Draw

mesh = Mesh(unit_square.GenerateMesh(maxh=0.05))

dS = dx(element_boundary=True)
n = specialcf.normal(2)
h = specialcf.mesh_size

We introduce the average $\{ u \}$ as a new variable living on facets:

In [ ]:
order = 2
# fesu = L2(mesh, order=order)
fesu = Discontinuous(H1(mesh, order=order))
fesu.SetCouplingType( IntRange(0, fesu.ndof), COUPLING_TYPE.INTERFACE_DOF)
fesuhat = FacetFESpace (mesh, order=order, dirichlet=".*")
fesg = PrivateSpace(VectorL2(mesh, order=order))
fesgt = PrivateSpace(VectorL2(mesh, order=order))

fes = fesu*fesuhat*fesg*fesgt

u,uhat,g,gt = fes.TrialFunction()
du,duhat,dg,dgt = fes.TestFunction()

print ("ndof = ", fes.ndof)

The LDG-gradient $g = g(u)$ is defined by:

$$
\int g \delta g = \sum_T \int_T \nabla u \delta g + \int_{\partial T} [u-\hat u] \delta g_n
$$

We are locally condensing out both $g$ variables:

In [ ]:
a = BilinearForm(fes, condense=True)

a += g*dg*dx
a += dgt*(g-grad(u))*dx + dgt*n*(u-uhat)*dS
a += gt*(dg-grad(du))*dx + gt*n*(du-duhat)*dS

#stabilization
a += 1/h*(u-uhat)*(du-duhat) *dS
a.Assemble();

print ("HDG non-zero-elements:", a.mat.nze)

In [ ]:
f = LinearForm(1*du*dx).Assemble()
gfu = GridFunction(fes)

inv = a.mat.Inverse(freedofs=fes.FreeDofs(), inverse="sparsecholesky")
print ("HDG inv non-zero-elements:", inv.nze)
gfu.vec.data = inv * f.vec

In [ ]:
Draw (gfu.components[0]);

We define the operator `makeboth` $u_T \mapsto (u_T, \{ u_T \})$

In [ ]:
eT,eF,*_ = fes.embeddings
# traceop = fesu.TraceOperator(fesuhat, average=True)
traceop = ConvertOperator(fesu, fesuhat, geom_free=True) # , vb=VOL)

projinner = Projector(fesuhat.GetDofs(mesh.Boundaries(".*")), False)
makeboth = (eF@projinner@traceop+eT)

DGop = makeboth.T @ a.mat @ makeboth

since the DGop is now a linear operator (not a sparse matrix), we have to use an iterative solver:

In [ ]:
inv = CGSolver(DGop, IdentityMatrix(fesu.ndof))
gfel = GridFunction(fesu)
gfel.vec.data = inv @ eT.T * f.vec

Draw (gfel);

In [ ]:
DGopmat = DGop.CreateSparseMatrix().DeleteZeroElements(1e-12)
print ("LDG nze = ", DGopmat.nze)
inv = DGopmat.Inverse(inverse="sparsecholesky")
print ("LDG inv nze = ", inv.nze)

gfel.vec.data = inv @ eT.T * f.vec
Draw (gfel);

to compare with a standard $H^1$-method:

In [ ]:
fes1 = H1(mesh, order=3, dirichlet=".*")
u1,v1 = fes1.TnT()
bfa1 = BilinearForm(grad(u1)*grad(v1)*dx).Assemble()
lff1 = LinearForm(v1*dx).Assemble()
gfu1 = GridFunction(fes1)
gfu1.vec.data = bfa1.mat.Inverse(freedofs=fes1.FreeDofs()) * lff1.vec
Draw (gfu1);